In [1]:
# Modules
import gurobipy as grb
import pandas as pd
import numpy as np
import math
import random

# Standard output divider
div = "-----"

# Print warning message


# Timeslots
alltimeslots = {
    1: "8:00am",
    2: "8:45am",
    3: "9:30am",
    4: "10:30am",
    5: "11:15am",
    6: "12:00pm",
    7: "1:15pm",
    8: "2:00pm",
    9: "2:45pm",
    10: "3:45pm",
    11: "4:30pm",
    12: "5:15pm",
    13: "6:30pm",
    14: "7:15pm",
    15: "8:00pm",
    16: "8:45pm"
}



# Dictionary of preference strings and corresponding values
preferencedict = {
    "Available, Prefer": 1,
    "Available, Neutral Preference": 2,
    "Available, Prefer Not": 3,
    "Unavailable": 4
}

# Dictionary of speaker vetos and corresponding values

vetodict = {
    "I would not like to veto any position": 0,
    "1st Speaker": 1,
    "2nd Speaker": 2,
    "3rd Speaker": 3,
}

vetodictinv = {
    0: "has no speaker position vetoes",
    1: "has vetoed 1st speaker",
    2: "has vetoed 2nd speaker",
    3: "has vetoed 3rd speaker"
}

# Person class
# - No preferences or vetoes for Easters trials

class person:
    name = ""
    
    # Speaker veto - 1 for 1st, 2 for 2nd, 3 for 3rd, 0 for no veto
    speakerveto = 0
 
    availabilities = {}
    
    def __init__(self,name,availabilities,speakerveto,isAllocated):
        self.name = name
        self.availabilities = availabilities
        self.speakerveto = speakerveto
        isAllocated = False
        
        
def importData():
    print("Please note the final allocation may take up to 10 minutes to compute.")
    global speakers
    speakers = []
    global times
    times = {}
    # CSV reading and parsing
    global csv
    csv = pd.read_csv("data.csv")
    csv.head()
    for index,row in csv.iterrows():
        if row[7] != "Adjudicating only": # MARK: Trial type
            avail = {}
            for i in range(14,29): # MARK: Range of trial slots
                avail[i-13] = preferencedict[row[i]] # MARK: Subtraction
            speakers.append(person(row[3],avail,vetodict[row[13]],False)) # MARK: Details

    # Calculate how many timeslots are required
    reqd = int(np.floor(len(speakers)/6))
    for key,value in alltimeslots.iteritems():
        if key <= reqd:
            times[key] = value
    print("A minimum of {} debates is required to distribute {} speakers.".format(reqd,len(speakers)))
    
    '''If the allocator produces an infeasible result there's a good chance it needs more timeslots.
    Manually override times with a higher number of slots if required'''
    
    for t in range(1,reqd):
        times[t] = alltimeslots[t]

    # Form the feasible team set
    global ftset
    global ftsample
    ftset = {}
    ftsample = {}
    totalteams = len(speakers)**3
    index = 1
    print("Forming Feasible Team Set...")
    for speaker1 in speakers:
        for speaker2 in speakers:
            for speaker3 in speakers:
                if speaker1 != speaker2 and speaker1 != speaker3 and speaker2 != speaker3:
                    if speaker1.speakerveto != 1 and speaker2.speakerveto != 2 and speaker3.speakerveto != 3:
                        print("Constructing team {} of {}...".format(index,totalteams))
                        ftset[index] = [speaker1,speaker2,speaker3]
                        index += 1
    
    randomkeys = random.sample(ftset.keys(), len(ftset)/100) # Vary so that a smaller subset is used for the fts
    for k in randomkeys:
        ftsample[k] = ftset[k]
    
    # Costs
    global costs
    costs = {}
    totalcosts = len(ftsample)*len(times)
    print("Calculating costs...")
    index2 = 1
    for key,team in ftsample.iteritems():
        for slot in times.keys():
            costs[key,slot] = 0
            index2 += 1
            print("Calculating cost {} of {}...".format(index2,totalcosts))
    
        # Time preferences
        '''Triallists are made aware that they may be called during "unavailable",
        so an 'unavailable' does not make the cost infinitely high, it just incurs
        a high cost.
        
        As slots become less desirable, the cost increases exponentially rather than
        linearly'''
    
        for speaker in team:
            for slot in times.keys():
                if speaker.availabilities[slot] == 4:
                    cost = grb.GRB.INFINITY
                else:
                    mag = speaker.availabilities[slot]*100
                    exp = mag**2
                    costs[key,slot] += exp
    
def allocate():
    # Optimisation
    a = grb.Model("2019 Easters Trial Allocator")
    x = {}
    for key,value in costs.iteritems():
        x[key] = a.addVar(vtype = grb.GRB.BINARY, obj = value, name = "x_{}".format(key))
        
    # Exactly 2 teams to each timeslot
    for slot in times.keys():
        a.addConstr(sum(x[team,slot] for team in ftsample.keys()) == 2)
        
    # Each team to no more than 1 timeslot
    for key,team in ftsample.iteritems():
        a.addConstr(sum(x[key,slot] for slot in times.keys()) <= 1)

    thirdvetoes = []
    for s in speakers:
        affectedTeams = []
        for key,team in ftsample.iteritems():
            if s in team:
                affectedTeams.append(key)
                
        # Each speaker to no more than 1 debate in 1 timeslot
        '''Can be 0 debates (ie. unallocated) and then appended
        as alternate 3rds'''
        a.addConstr(sum(x[team,slot] for team in affectedTeams for slot in times.keys()) <= 1)
        
        if s.speakerveto == 3:
            thirdvetoes.append(s)
            
    # Speakers who veto 3rd must be in exactly 1 timeslot
    '''3rd vetoes cannot be unallocated and then tacked on as
    alternate 3rds, so they must be allocated in a debate.'''
    for speaker in thirdvetoes:
        affectedTeams2 = []
        for key,team in ftsample.iteritems():
            if speaker in team:
                affectedTeams2.append(key)
        a.addConstr(sum(x[team,slot] for team in affectedTeams2 for slot in times.keys()) == 1)
    
    a.modelSense = grb.GRB.MINIMIZE
    a.optimize()
    allocated = []
    unallocated = []
    unallocatednames = []
    print(div)
    print("USU EASTERS TRIALS 2019 - DEBATE ALLOCATION")
    print("Speakers in each team are listed in speaking order.")
    print("Sides for each debate should be determined randomly.")
    print(div)
    for key,value in costs.iteritems():
        if x[key].x != 0:
            spk = []
            for s in ftsample[key[0]]:
                spk.append(s.name)
            print("Team {} {} at {}".format(key[0],spk,times[key[1]]))
            for speaker in ftsample[key[0]]:
                speaker.isAllocated = True
                allocated.append(speaker.name)
    for speaker in speakers:
        if speaker.name not in allocated:#if speaker.isAllocated == False:
            unallocated.append(speaker)
            unallocatednames.append(speaker.name)
    print("Total Cost: {}".format(a.objVal))
    print(div)
    
    j = ", "
    print("Unallocated Speakers: {}".format(j.join(unallocatednames)))
    print(div)
    report(unallocated)

def report(speakers):
    for speaker in speakers:
        if speaker not in speakers:
            print("Speaker {} does not exist".format(speaker.name))
        else:
            vetoString= "{} {}.".format(speaker.name, vetodictinv[speaker.speakerveto])

            print("Report for {}".format(speaker.name))
            print(vetoString)
            print("{}'s availability is as follows:".format(speaker.name))
            for slot,availability in speaker.availabilities.iteritems():
                try:
                    # TODO
                    pass
                    #print("{}: {}".format(times[slot],availability))
                except:
                    pass
        print(div)

In [2]:
importData()

Please note the final allocation may take up to 10 minutes to compute.
A minimum of 12 debates is required to distribute 72 speakers.
Forming Feasible Team Set...
Constructing team 1 of 373248...
Constructing team 2 of 373248...
Constructing team 3 of 373248...
Constructing team 4 of 373248...
Constructing team 5 of 373248...
Constructing team 6 of 373248...
Constructing team 7 of 373248...
Constructing team 8 of 373248...
Constructing team 9 of 373248...
Constructing team 10 of 373248...
Constructing team 11 of 373248...
Constructing team 12 of 373248...
Constructing team 13 of 373248...
Constructing team 14 of 373248...
Constructing team 15 of 373248...
Constructing team 16 of 373248...
Constructing team 17 of 373248...
Constructing team 18 of 373248...
Constructing team 19 of 373248...
Constructing team 20 of 373248...
Constructing team 21 of 373248...
Constructing team 22 of 373248...
Constructing team 23 of 373248...
Constructing team 24 of 373248...
Constructing team 25 of 373248

Constructing team 1122 of 373248...
Constructing team 1123 of 373248...
Constructing team 1124 of 373248...
Constructing team 1125 of 373248...
Constructing team 1126 of 373248...
Constructing team 1127 of 373248...
Constructing team 1128 of 373248...
Constructing team 1129 of 373248...
Constructing team 1130 of 373248...
Constructing team 1131 of 373248...
Constructing team 1132 of 373248...
Constructing team 1133 of 373248...
Constructing team 1134 of 373248...
Constructing team 1135 of 373248...
Constructing team 1136 of 373248...
Constructing team 1137 of 373248...
Constructing team 1138 of 373248...
Constructing team 1139 of 373248...
Constructing team 1140 of 373248...
Constructing team 1141 of 373248...
Constructing team 1142 of 373248...
Constructing team 1143 of 373248...
Constructing team 1144 of 373248...
Constructing team 1145 of 373248...
Constructing team 1146 of 373248...
Constructing team 1147 of 373248...
Constructing team 1148 of 373248...
Constructing team 1149 of 37

Constructing team 2124 of 373248...
Constructing team 2125 of 373248...
Constructing team 2126 of 373248...
Constructing team 2127 of 373248...
Constructing team 2128 of 373248...
Constructing team 2129 of 373248...
Constructing team 2130 of 373248...
Constructing team 2131 of 373248...
Constructing team 2132 of 373248...
Constructing team 2133 of 373248...
Constructing team 2134 of 373248...
Constructing team 2135 of 373248...
Constructing team 2136 of 373248...
Constructing team 2137 of 373248...
Constructing team 2138 of 373248...
Constructing team 2139 of 373248...
Constructing team 2140 of 373248...
Constructing team 2141 of 373248...
Constructing team 2142 of 373248...
Constructing team 2143 of 373248...
Constructing team 2144 of 373248...
Constructing team 2145 of 373248...
Constructing team 2146 of 373248...
Constructing team 2147 of 373248...
Constructing team 2148 of 373248...
Constructing team 2149 of 373248...
Constructing team 2150 of 373248...
Constructing team 2151 of 37

Constructing team 3216 of 373248...
Constructing team 3217 of 373248...
Constructing team 3218 of 373248...
Constructing team 3219 of 373248...
Constructing team 3220 of 373248...
Constructing team 3221 of 373248...
Constructing team 3222 of 373248...
Constructing team 3223 of 373248...
Constructing team 3224 of 373248...
Constructing team 3225 of 373248...
Constructing team 3226 of 373248...
Constructing team 3227 of 373248...
Constructing team 3228 of 373248...
Constructing team 3229 of 373248...
Constructing team 3230 of 373248...
Constructing team 3231 of 373248...
Constructing team 3232 of 373248...
Constructing team 3233 of 373248...
Constructing team 3234 of 373248...
Constructing team 3235 of 373248...
Constructing team 3236 of 373248...
Constructing team 3237 of 373248...
Constructing team 3238 of 373248...
Constructing team 3239 of 373248...
Constructing team 3240 of 373248...
Constructing team 3241 of 373248...
Constructing team 3242 of 373248...
Constructing team 3243 of 37

Constructing team 4290 of 373248...
Constructing team 4291 of 373248...
Constructing team 4292 of 373248...
Constructing team 4293 of 373248...
Constructing team 4294 of 373248...
Constructing team 4295 of 373248...
Constructing team 4296 of 373248...
Constructing team 4297 of 373248...
Constructing team 4298 of 373248...
Constructing team 4299 of 373248...
Constructing team 4300 of 373248...
Constructing team 4301 of 373248...
Constructing team 4302 of 373248...
Constructing team 4303 of 373248...
Constructing team 4304 of 373248...
Constructing team 4305 of 373248...
Constructing team 4306 of 373248...
Constructing team 4307 of 373248...
Constructing team 4308 of 373248...
Constructing team 4309 of 373248...
Constructing team 4310 of 373248...
Constructing team 4311 of 373248...
Constructing team 4312 of 373248...
Constructing team 4313 of 373248...
Constructing team 4314 of 373248...
Constructing team 4315 of 373248...
Constructing team 4316 of 373248...
Constructing team 4317 of 37

...

Calculating cost 14580 of 18840...
Calculating cost 14581 of 18840...
Calculating cost 14582 of 18840...
Calculating cost 14583 of 18840...
Calculating cost 14584 of 18840...
Calculating cost 14585 of 18840...
Calculating cost 14586 of 18840...
Calculating cost 14587 of 18840...
Calculating cost 14588 of 18840...
Calculating cost 14589 of 18840...
Calculating cost 14590 of 18840...
Calculating cost 14591 of 18840...
Calculating cost 14592 of 18840...
Calculating cost 14593 of 18840...
Calculating cost 14594 of 18840...
Calculating cost 14595 of 18840...
Calculating cost 14596 of 18840...
Calculating cost 14597 of 18840...
Calculating cost 14598 of 18840...
Calculating cost 14599 of 18840...
Calculating cost 14600 of 18840...
Calculating cost 14601 of 18840...
Calculating cost 14602 of 18840...
Calculating cost 14603 of 18840...
Calculating cost 14604 of 18840...
Calculating cost 14605 of 18840...
Calculating cost 14606 of 18840...
Calculating cost 14607 of 18840...
Calculating cost 146

Calculating cost 15565 of 18840...
Calculating cost 15566 of 18840...
Calculating cost 15567 of 18840...
Calculating cost 15568 of 18840...
Calculating cost 15569 of 18840...
Calculating cost 15570 of 18840...
Calculating cost 15571 of 18840...
Calculating cost 15572 of 18840...
Calculating cost 15573 of 18840...
Calculating cost 15574 of 18840...
Calculating cost 15575 of 18840...
Calculating cost 15576 of 18840...
Calculating cost 15577 of 18840...
Calculating cost 15578 of 18840...
Calculating cost 15579 of 18840...
Calculating cost 15580 of 18840...
Calculating cost 15581 of 18840...
Calculating cost 15582 of 18840...
Calculating cost 15583 of 18840...
Calculating cost 15584 of 18840...
Calculating cost 15585 of 18840...
Calculating cost 15586 of 18840...
Calculating cost 15587 of 18840...
Calculating cost 15588 of 18840...
Calculating cost 15589 of 18840...
Calculating cost 15590 of 18840...
Calculating cost 15591 of 18840...
Calculating cost 15592 of 18840...
Calculating cost 155

Calculating cost 16698 of 18840...
Calculating cost 16699 of 18840...
Calculating cost 16700 of 18840...
Calculating cost 16701 of 18840...
Calculating cost 16702 of 18840...
Calculating cost 16703 of 18840...
Calculating cost 16704 of 18840...
Calculating cost 16705 of 18840...
Calculating cost 16706 of 18840...
Calculating cost 16707 of 18840...
Calculating cost 16708 of 18840...
Calculating cost 16709 of 18840...
Calculating cost 16710 of 18840...
Calculating cost 16711 of 18840...
Calculating cost 16712 of 18840...
Calculating cost 16713 of 18840...
Calculating cost 16714 of 18840...
Calculating cost 16715 of 18840...
Calculating cost 16716 of 18840...
Calculating cost 16717 of 18840...
Calculating cost 16718 of 18840...
Calculating cost 16719 of 18840...
Calculating cost 16720 of 18840...
Calculating cost 16721 of 18840...
Calculating cost 16722 of 18840...
Calculating cost 16723 of 18840...
Calculating cost 16724 of 18840...
Calculating cost 16725 of 18840...
Calculating cost 167

Calculating cost 17642 of 18840...
Calculating cost 17643 of 18840...
Calculating cost 17644 of 18840...
Calculating cost 17645 of 18840...
Calculating cost 17646 of 18840...
Calculating cost 17647 of 18840...
Calculating cost 17648 of 18840...
Calculating cost 17649 of 18840...
Calculating cost 17650 of 18840...
Calculating cost 17651 of 18840...
Calculating cost 17652 of 18840...
Calculating cost 17653 of 18840...
Calculating cost 17654 of 18840...
Calculating cost 17655 of 18840...
Calculating cost 17656 of 18840...
Calculating cost 17657 of 18840...
Calculating cost 17658 of 18840...
Calculating cost 17659 of 18840...
Calculating cost 17660 of 18840...
Calculating cost 17661 of 18840...
Calculating cost 17662 of 18840...
Calculating cost 17663 of 18840...
Calculating cost 17664 of 18840...
Calculating cost 17665 of 18840...
Calculating cost 17666 of 18840...
Calculating cost 17667 of 18840...
Calculating cost 17668 of 18840...
Calculating cost 17669 of 18840...
Calculating cost 176

Calculating cost 18678 of 18840...
Calculating cost 18679 of 18840...
Calculating cost 18680 of 18840...
Calculating cost 18681 of 18840...
Calculating cost 18682 of 18840...
Calculating cost 18683 of 18840...
Calculating cost 18684 of 18840...
Calculating cost 18685 of 18840...
Calculating cost 18686 of 18840...
Calculating cost 18687 of 18840...
Calculating cost 18688 of 18840...
Calculating cost 18689 of 18840...
Calculating cost 18690 of 18840...
Calculating cost 18691 of 18840...
Calculating cost 18692 of 18840...
Calculating cost 18693 of 18840...
Calculating cost 18694 of 18840...
Calculating cost 18695 of 18840...
Calculating cost 18696 of 18840...
Calculating cost 18697 of 18840...
Calculating cost 18698 of 18840...
Calculating cost 18699 of 18840...
Calculating cost 18700 of 18840...
Calculating cost 18701 of 18840...
Calculating cost 18702 of 18840...
Calculating cost 18703 of 18840...
Calculating cost 18704 of 18840...
Calculating cost 18705 of 18840...
Calculating cost 187

In [3]:
allocate()

Optimize a model with 1675 rows, 18840 columns and 108576 nonzeros
Variable types: 0 continuous, 18840 integer (18840 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+04, 3e+05]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 2e+00]
Presolve removed 1591 rows and 252 columns
Presolve time: 0.29s
Presolved: 84 rows, 18588 columns, 74352 nonzeros
Variable types: 0 continuous, 18588 integer (18588 binary)

Root relaxation: objective 2.000000e+04, 343 iterations, 0.12 seconds

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0 20000.0000    0   79          - 20000.0000      -     -    0s
H    0     0                    20000.000000 20000.0000  0.00%     -    1s

Explored 1 nodes (770 simplex iterations) in 1.11 seconds
Thread count was 4 (of 4 available processors)

Solution count 1: 20000 

Optimal solution found (tolerance 1